# MS Data Analysis Tools

## Load Data

**Input:**
-   `.tsv` file obtained as an output of `preprocessing_template.ipynb`

In [1]:
%matplotlib inline

import pandas as pd
from MSprocessing.stats.utils import split_data, within_group_corr, within_between_corr
from MSprocessing.stats.plots import volcano_plot, plot_heatmap, plot_venn
from MSprocessing.stats.ttests import run_dea
from MSprocessing.stats.models import run_mixedlm
from MSprocessing.stats.enrichment import go_enrichment, convert_ids

In [2]:
index_cols = ["label_id", "group", "AL_kode", "plate_position", "plate_nr",
 "sample_name", "sample_type", "study_ID", "timepoint", "sample_order"]

data = pd.read_csv("preprocessed_data.tsv", sep="\t", index_col=index_cols)
data = data[data.index.get_level_values("sample_type") == "sample"].copy()

In [6]:
proteome, meta = split_data(data, "sample_name") #set column to use as index
proteome

nan_fraction  A0A075B6H9  A0A075B6I9  A0A075B6J1  A0A075B6J2  \
sample_name                                                                 
plate1_A6        0.234093      17.760      26.400      18.948      18.299   
plate1_A7        0.330715      18.806      28.158      19.665      17.762   
plate1_A8        0.311076      18.697      27.560      21.499      19.810   
plate1_A9        0.259230      21.191      27.411      20.198      19.571   
plate1_A10       0.256088      18.598      26.155      21.587      19.858   
...                   ...         ...         ...         ...         ...   
plate2_E10       0.306363      19.997      27.647      20.459      18.647   
plate2_E11       0.305577      17.401      27.823      21.113      19.396   
plate2_E12       0.297722      17.754      27.521      23.013      20.292   
plate2_F1        0.335428      18.510      26.539      19.971      19.457   
plate2_F2        0.352710      19.747      27.239      20.724      20.225   

             A0A075B6J9  A0A075B6K0  A0A075B6K2  A0A075B6K4  A0A075B6K5  ...  \
sample_name                                                              ...   
plate1_A6        24.033      22.404      17.002      25.341      27.624  ...   
plate1_A7        23.133      23.537      20.572      25.321      27.161  ...   
plate1_A8        25.523      23.853      18.957      26.426      28.127  ...   
plate1_A9        24.972      24.491      19.192      24.577      27.163  ...   
plate1_A10       24.816      24.733      19.707      24.409      28.268  ...   
...                 ...         ...         ...         ...         ...  ...   
plate2_E10       24.934      24.071      19.837      24.770      27.464  ...   
plate2_E11       23.994      25.509      21.249      27.115      27.878  ...   
plate2_E12       24.894      24.977      18.693      25.827      27.838  ...   
plate2_F1        25.095      25.903      19.515      27.280      29.471  ...   
plate2_F2        24.157      25.225      19.122      26.800      27.717  ...   

             Q9Y608  Q9Y613  Q9Y624  Q9Y646  Q9Y696  Q9Y6C2  Q9Y6E0  Q9Y6N7  \
sample_name                                                                   
plate1_A6    16.801  17.456  19.491  15.326  16.259  13.916  18.166  13.187   
plate1_A7    16.274  16.749  19.086  15.086  16.496  13.708  16.566  13.359   
plate1_A8    16.719  16.764  18.876  15.716  16.956  13.466  17.061  13.647   
plate1_A9    15.696  16.112  19.398  15.872  17.277  12.500  17.700  12.975   
plate1_A10   16.190  16.597  19.942  15.909  16.789  13.447  17.849  13.270   
...             ...     ...     ...     ...     ...     ...     ...     ...   
plate2_E10   15.660  16.876  18.204  16.554  16.569  12.899  16.863  13.164   
plate2_E11   17.519  15.896  19.650  16.126  17.181  13.710  16.807  13.375   
plate2_E12   18.594  16.834  17.827  16.725  17.077  13.441  17.575  13.008   
plate2_F1    17.465  16.384  19.689  16.656  17.387  13.586  17.424  13.914   
plate2_F2    16.681  17.067  19.467  17.170  16.869  14.060  17.763  13.881   

             Q9Y6R7  Q9Y6Z7  
sample_name                  
plate1_A6    22.804  22.448  
plate1_A7    22.018  22.832  
plate1_A8    22.227  21.812  
plate1_A9    23.834  22.154  
plate1_A10   22.755  23.075  
...             ...     ...  
plate2_E10   21.957  22.726  
plate2_E11   23.642  23.817  
plate2_E12   25.336  23.748  
plate2_F1    21.579  22.358  
plate2_F2    23.477  23.961  

[148 rows x 1273 columns]

In [7]:
meta

label_id         group  AL_kode plate_position plate_nr  \
sample_name                                                              
plate1_A6    4083906373  Intervention   100005             A6   plate1   
plate1_A7    4083918930  Intervention   100006             A7   plate1   
plate1_A8    4083982663  Intervention   100007             A8   plate1   
plate1_A9    4083907917       Control   100008             A9   plate1   
plate1_A10   4083985725  Intervention   100009            A10   plate1   
...                 ...           ...      ...            ...      ...   
plate2_E10   4083996660       Control   100153            E10   plate2   
plate2_E11   4083980445  Intervention   100154            E11   plate2   
plate2_E12   4083966190  Intervention   100155            E12   plate2   
plate2_F1    4083947093       Control   100156             F1   plate2   
plate2_F2    4083966929  Intervention   100157             F2   plate2   

            sample_type  study_ID timepoint  sample_order  
sample_name                                                
plate1_A6        sample      67.0    day_15             1  
plate1_A7        sample      34.0     day_0             2  
plate1_A8        sample      63.0     day_0             3  
plate1_A9        sample      16.0    day_15             4  
plate1_A10       sample      79.0     day_0             5  
...                 ...       ...       ...           ...  
plate2_E10       sample      57.0     day_0           148  
plate2_E11       sample      79.0    day_15           149  
plate2_E12       sample      35.0    day_15           150  
plate2_F1        sample      45.0    day_15           151  
plate2_F2        sample       5.0     day_0           152  

[148 rows x 9 columns]

### Exploratory Analysis

In [8]:
plot_heatmap(
    proteome, 
    meta, 
    group_by=["study_ID", "group"]
    )

In [9]:
#calculate the correlation between samples of the same group and with samples outside of the group

corr_ext = within_between_corr(proteome, meta, id_col="study_ID", method="pearson")
print(f"Mean within-patient corr:  {corr_ext['within_mean']:.3f}")
print(f"Mean between-patient corr: {corr_ext['between_mean']:.3f}")

Mean within-patient corr:  -0.021
Mean between-patient corr: -0.006


### Differential Expression Analysis

In [10]:
meta

label_id         group  AL_kode plate_position plate_nr  \
sample_name                                                              
plate1_A6    4083906373  Intervention   100005             A6   plate1   
plate1_A7    4083918930  Intervention   100006             A7   plate1   
plate1_A8    4083982663  Intervention   100007             A8   plate1   
plate1_A9    4083907917       Control   100008             A9   plate1   
plate1_A10   4083985725  Intervention   100009            A10   plate1   
...                 ...           ...      ...            ...      ...   
plate2_E10   4083996660       Control   100153            E10   plate2   
plate2_E11   4083980445  Intervention   100154            E11   plate2   
plate2_E12   4083966190  Intervention   100155            E12   plate2   
plate2_F1    4083947093       Control   100156             F1   plate2   
plate2_F2    4083966929  Intervention   100157             F2   plate2   

            sample_type  study_ID timepoint  sample_order  
sample_name                                                
plate1_A6        sample      67.0    day_15             1  
plate1_A7        sample      34.0     day_0             2  
plate1_A8        sample      63.0     day_0             3  
plate1_A9        sample      16.0    day_15             4  
plate1_A10       sample      79.0     day_0             5  
...                 ...       ...       ...           ...  
plate2_E10       sample      57.0     day_0           148  
plate2_E11       sample      79.0    day_15           149  
plate2_E12       sample      35.0    day_15           150  
plate2_F1        sample      45.0    day_15           151  
plate2_F2        sample       5.0     day_0           152  

[148 rows x 9 columns]

In [20]:
dea_results = run_dea(
    proteome=proteome,
    meta=meta,
    group_col="group",
    group1="Intervention",
    group2="Control",
    adjust="stepdown_perm",
    n_perm=10000,
    method="student_ttest",
)

dea_results


log2fc      pval      padj
protein                                 
A0A0C4DH32 -0.457200  0.000787  0.000700
Q14247     -0.419894  0.001068  0.001800
P02745      0.356462  0.004370  0.012299
P62834     -0.333084  0.009275  0.035796
P00338      0.228261  0.010926  0.054495
...              ...       ...       ...
Q13094      0.000383  0.997467  1.000000
P32004      0.000196  0.998308  1.000000
Q9HCN6      0.000217  0.998447  1.000000
Q5SQ64     -0.000102  0.999184  1.000000
Q96PD5     -0.000084  0.999428  1.000000

[1273 rows x 3 columns]

In [22]:
print(dea_results.loc["Q14247"])
print(dea_results.loc["A0A087WSY6"])
print(dea_results.loc["Q96BM9;Q9NVJ2"])

log2fc   -0.419894
pval      0.001068
padj      0.001800
Name: Q14247, dtype: float64
log2fc   -0.218402
pval      0.145025
padj      1.000000
Name: A0A087WSY6, dtype: float64
log2fc    0.139359
pval      0.048982
padj      0.880012
Name: Q96BM9;Q9NVJ2, dtype: float64


In [21]:
volcano_plot(dea_results, alpha=0.05, labels = False)


In [23]:
convert_ids(dea_results, from_type="uniprot", to_type="symbol").head(4)

WARNING	Task(Task-2) biothings.client:iteration.py:concatenate_list()- Input sequence provided is already in string format. No operation performed
WARNING	Task(Task-2) biothings.client:iteration.py:concatenate_list()- Input sequence provided is already in string format. No operation performed
INFO	Task(Task-2) biothings.client:base.py:_repeated_query()- querying 1-1000 ...
INFO	Task(Task-2) biothings.client:base.py:_repeated_query()- querying 1001-1273 ...
INFO	Task(Task-2) biothings.client:base.py:_querymany()- Finished.
WARNING	Task(Task-2) biothings.client:base.py:_querymany()- 11 input query terms found dup hits:	[('P04908', 2), ('P62805', 10), ('P59665', 2), ('P0DP23', 3), ('P0DMV8', 2), ('P84243', 2), ('P0C0L5
WARNING	Task(Task-2) biothings.client:base.py:_querymany()- 114 input query terms found no hit:	['A0A0C4DH32', 'P0DOY2', 'P01877', 'P01700', 'A0A075B6R2', 'A0A0C4DH39', 'A0A0C4DH30', 'A0A0C4DH35',
INFO	Task(Task-2) biothings.client:base.py:_querymany()- Pass "returnall=True

log2fc      pval      padj
A0A0C4DH32 -0.457200  0.000787  0.000700
CTTN       -0.419894  0.001068  0.001800
C1QA        0.356462  0.004370  0.012299
RAP1A      -0.333084  0.009275  0.035796

### Mixed LM

In [25]:
lmm_results = run_mixedlm(
    proteome, 
    meta, 
    formula="y ~ timepoint", 
    group_col="study_ID", 
    adjust="fdr_bh", 
    reml=True,
    filter_to="timepoint"
    )

lmm_results

Defaulted to OLS for A0A075B6S5
Defaulted to OLS for A0A0C4DH34
Defaulted to OLS for A0A0C4DH72
Defaulted to OLS for A0A0J9YX35
Defaulted to OLS for A0M8Q6
Defaulted to OLS for O15394
Defaulted to OLS for O43184
Defaulted to OLS for O43294
Defaulted to OLS for P01137
Defaulted to OLS for P02655
Defaulted to OLS for P05387
Defaulted to OLS for P08238
Defaulted to OLS for P08670
Defaulted to OLS for P08833
Defaulted to OLS for P11277
Defaulted to OLS for P11465
Defaulted to OLS for P11586
Defaulted to OLS for P13501
Defaulted to OLS for P13598
Defaulted to OLS for P13639
Defaulted to OLS for P13647
Defaulted to OLS for P13688
Defaulted to OLS for P15907
Defaulted to OLS for P21980
Defaulted to OLS for P22314
Defaulted to OLS for P23142
Defaulted to OLS for P23368
Defaulted to OLS for P25705
Defaulted to OLS for P27918
Defaulted to OLS for P29622
Defaulted to OLS for P34932
Defaulted to OLS for P48735
Defaulted to OLS for P51149
Defaulted to OLS for P63241;Q6IS14;Q9GZV4
Defaulted to OLS f

coef      pval      padj
protein                                 
P01130     -0.375829  0.013974  0.742675
P27918      0.286729  0.017330  0.742675
Q16851      0.257457  0.019876  0.742675
Q96DR8     -0.213343  0.021031  0.742675
A0A0C4DH72  0.320071  0.022236  0.742675
...              ...       ...       ...
Q9HCB6      0.002943  0.975451  0.994560
Q93088     -0.001929  0.982176  0.994560
Q13232      0.001600  0.985813  0.994560
A0A0C4DH38 -0.001000  0.994274  0.994560
P22314     -0.000771  0.994560  0.994560

[167 rows x 3 columns]

## GO Enrichment

In [26]:
enrichment_ttest = go_enrichment(dea_results, restrict_background=True, adjust="fdr")
enrichment_ttest

source      native                                       name   p_value  \
0    GO:CC  GO:0005602            complement component C1 complex  0.079232   
1    GO:CC  GO:0062167           complement component C1q complex  0.079232   
2    GO:CC  GO:0008076    voltage-gated potassium channel complex  0.079232   
3    GO:CC  GO:0032045  guanyl-nucleotide exchange factor complex  0.079232   
4    GO:CC  GO:0034705                  potassium channel complex  0.079232   
..     ...         ...                                        ...       ...   
621  GO:CC  GO:0043226                                  organelle  0.985318   
622  GO:CC  GO:0043227                 membrane-bounded organelle  0.985318   
623  GO:CC  GO:0043230                    extracellular organelle  0.985318   
624  GO:CC  GO:1903561                      extracellular vesicle  0.985318   
625  GO:CC  GO:0005615                        extracellular space  0.991147   

     significant                                        description  \
0          False  "A protein complex composed of six subunits of...   
1          False  "A protein-containing complex composed of six ...   
2          False  "A protein complex that forms a transmembrane ...   
3          False  "A protein complex that stimulates the exchang...   
4          False  "An ion channel complex through which potassiu...   
..           ...                                                ...   
621        False  "Organized structure of distinctive morphology...   
622        False  "Organized structure of distinctive morphology...   
623        False  "Organized structure of distinctive morphology...   
624        False  "Any vesicle that is part of the extracellular...   
625        False  "That part of a multicellular organism outside...   

     term_size  query_size  intersection_size  effective_domain_size  \
0            2           4                  1                   1255   
1            2           4                  1                   1255   
2            2           4                  1                   1255   
3            1           4                  1                   1255   
4            2           4                  1                   1255   
..         ...         ...                ...                    ...   
621       1016           4                  2                   1255   
622        972           4                  2                   1255   
623        655           4                  1                   1255   
624        655           4                  1                   1255   
625        869           4                  1                   1255   

     precision    recall    query                   parents  
0         0.25  0.500000  query_1  [GO:0005576, GO:0032991]  
1         0.25  0.500000  query_1  [GO:0005576, GO:0032991]  
2         0.25  0.500000  query_1  [GO:0034705, GO:0098797]  
3         0.25  1.000000  query_1              [GO:0140535]  
4         0.25  0.500000  query_1              [GO:0034703]  
..         ...       ...      ...                       ...  
621       0.50  0.001969  query_1              [GO:0110165]  
622       0.50  0.002058  query_1              [GO:0043226]  
623       0.25  0.001527  query_1  [GO:0005576, GO:0043226]  
624       0.25  0.001527  query_1  [GO:0031982, GO:0065010]  
625       0.25  0.001151  query_1  [GO:0005576, GO:0110165]  

[626 rows x 14 columns]